<a href="https://colab.research.google.com/github/Shilpa393/Sql_Codes/blob/main/Shilpa_Sen_3D_Exercise.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

![alt text](https://github.com/Praxis-QR/RDWH/raw/main/images/YantraJaalBanner.png)<br>


<hr>

[Prithwis Mukerjee](http://www.linkedin.com/in/prithwis)<br>

PostgreSQL Tutorial based on https://www.postgresqltutorial.com/

##This Notebook consists of four parts. In total there are 200 queries out of which 41 are basic queries, 45 queries are on join, 90 queries are on aggregates, and 24 queries are on date.

In [ ]:
from datetime import datetime
import pytz
print('मिले सुर मेरा तुम्हारा, तो सुर बने हमारा',datetime.now(pytz.timezone('Asia/Calcutta')))
!python --version
!lsb_release -a

मिले सुर मेरा तुम्हारा, तो सुर बने हमारा 2024-03-04 10:30:20.425982+05:30
Python 3.10.12
No LSB modules are available.
Distributor ID:	Ubuntu
Description:	Ubuntu 22.04.3 LTS
Release:	22.04
Codename:	jammy


#Setup

In [ ]:
# Install postgresql server

!apt update > /dev/null
!apt install postgresql > /dev/null
#
import psycopg2
import pandas as pd
#!sudo -u postgres psql -V
!psql -V
!service postgresql start





psql (PostgreSQL) 14.11 (Ubuntu 14.11-0ubuntu0.22.04.1)
 * Starting PostgreSQL 14 database server
   ...done.


In [ ]:
# The install process creates an Ubuntu user 'postgres' AND a Postgres database user 'postgres' both of which are superusers
#!cat /etc/passwd
# Use these users to create a new database user called 'upraxis' and give it a password 'upass'
#!sudo -u postgres createuser --superuser upraxis
!sudo -u postgres createuser upraxis
!sudo -u postgres psql -U postgres -c "ALTER USER upraxis PASSWORD 'upass';"
# Change the database superuser 'postgres' to a non-default value 'pass'
!sudo -u postgres psql -U postgres -c "ALTER USER postgres PASSWORD 'pass';"
# Use ubuntu superuser to create database dvdrental and set its owner to upraxis
!sudo -u postgres createdb -O upraxis dvdrental
#
# Create file to store the password. Else will be prompted each time
!echo "localhost:5432:dvdrental:postgres:pass" > ~/.pgpass
!echo "localhost:5432:dvdrental:upraxis:upass" >> ~/.pgpass
!chmod 0600 ~/.pgpass
!cat ~/.pgpass

ALTER ROLE
ALTER ROLE
localhost:5432:dvdrental:postgres:pass
localhost:5432:dvdrental:upraxis:upass


## Create, Load Data

In [ ]:
!wget -q https://github.com/Praxis-QR/RDWH/raw/main/data/dvdrental.zip
#!wget https://www.postgresqltutorial.com/wp-content/uploads/2019/05/dvdrental.zip
!unzip dvdrental.zip
!ls dvd*.*

Archive:  dvdrental.zip
  inflating: dvdrental.tar           
dvdrental.tar  dvdrental.zip


In [ ]:
# Need the Ubuntu user postgres to run the pg_restore utility to recreate database from export
#
!sudo -u postgres pg_restore -d dvdrental /content/dvdrental.tar

In [ ]:
# 15 tables created and loaded with data
!psql -h localhost -p 5432 -U postgres -d dvdrental -c '\dt+ public.*'

                                         List of relations
 Schema |     Name      | Type  |  Owner   | Persistence | Access method |    Size    | Description 
--------+---------------+-------+----------+-------------+---------------+------------+-------------
 public | actor         | table | postgres | permanent   | heap          | 48 kB      | 
 public | address       | table | postgres | permanent   | heap          | 144 kB     | 
 public | category      | table | postgres | permanent   | heap          | 8192 bytes | 
 public | city          | table | postgres | permanent   | heap          | 96 kB      | 
 public | country       | table | postgres | permanent   | heap          | 40 kB      | 
 public | customer      | table | postgres | permanent   | heap          | 160 kB     | 
 public | film          | table | postgres | permanent   | heap          | 464 kB     | 
 public | film_actor    | table | postgres | permanent   | heap          | 304 kB     | 
 public | film_category | t

![alt text](https://raw.githubusercontent.com/Praxis-QR/RDWH/main/images/dvd-rental-sample-database-diagram.png)<br>

In [ ]:
!psql -h localhost -p 5432 -U postgres -d dvdrental -c 'select * from actor limit 10'
#the date data should have loaded correctly

 actor_id | first_name |  last_name   |      last_update       
----------+------------+--------------+------------------------
        1 | Penelope   | Guiness      | 2013-05-26 14:47:57.62
        2 | Nick       | Wahlberg     | 2013-05-26 14:47:57.62
        3 | Ed         | Chase        | 2013-05-26 14:47:57.62
        4 | Jennifer   | Davis        | 2013-05-26 14:47:57.62
        5 | Johnny     | Lollobrigida | 2013-05-26 14:47:57.62
        6 | Bette      | Nicholson    | 2013-05-26 14:47:57.62
        7 | Grace      | Mostel       | 2013-05-26 14:47:57.62
        8 | Matthew    | Johansson    | 2013-05-26 14:47:57.62
        9 | Joe        | Swank        | 2013-05-26 14:47:57.62
       10 | Christian  | Gable        | 2013-05-26 14:47:57.62
(10 rows)



In [ ]:
# check users and their authority
!psql -h localhost -p 5432 -U postgres -d dvdrental -c '\du'

                                   List of roles
 Role name |                         Attributes                         | Member of 
-----------+------------------------------------------------------------+-----------
 postgres  | Superuser, Create role, Create DB, Replication, Bypass RLS | {}
 upraxis   |                                                            | {}



In [ ]:
# Grant access to user upraxis
!psql -h localhost -p 5432 -U postgres -d dvdrental -c 'GRANT INSERT, UPDATE, SELECT, DELETE ON ALL TABLES IN SCHEMA public TO upraxis;'

GRANT


In [ ]:
!psql -h localhost -p 5432 -U upraxis -d dvdrental -c 'select * from actor limit 10'
#the date data should have loaded correctly

 actor_id | first_name |  last_name   |      last_update       
----------+------------+--------------+------------------------
        1 | Penelope   | Guiness      | 2013-05-26 14:47:57.62
        2 | Nick       | Wahlberg     | 2013-05-26 14:47:57.62
        3 | Ed         | Chase        | 2013-05-26 14:47:57.62
        4 | Jennifer   | Davis        | 2013-05-26 14:47:57.62
        5 | Johnny     | Lollobrigida | 2013-05-26 14:47:57.62
        6 | Bette      | Nicholson    | 2013-05-26 14:47:57.62
        7 | Grace      | Mostel       | 2013-05-26 14:47:57.62
        8 | Matthew    | Johansson    | 2013-05-26 14:47:57.62
        9 | Joe        | Swank        | 2013-05-26 14:47:57.62
       10 | Christian  | Gable        | 2013-05-26 14:47:57.62
(10 rows)



## Python Access
https://www.tutorialspoint.com/python_data_access/python_postgresql_database_connection.htm

In [ ]:
def runSelect(s):
    #Set up connection

    conn = psycopg2.connect(database="dvdrental", user='upraxis', password='upass', host='127.0.0.1', port= '5432')
    #Setting auto commit true
    conn.autocommit = True
    #Creating a cursor object using the cursor() method
    cursor = conn.cursor()
    #Retrieving data
    cursor.execute(s)
    #Fetching all rows from the table
    result = cursor.fetchall();
    #print(len(result))
    if (len(result)) > 0:                                       # result contains at least one row
        colnames = [desc[0] for desc in cursor.description]     # get column names
        #print(colnames)
        resultdf = pd.DataFrame(result)                         # convert list to dataframe
        resultdf.columns = colnames                             # add column names
        #return resultdf
        return resultdf.style.hide()                            # hide the index
    else:
        print('no records found')
        return

def runCmd(s):
    #Create Connection
    conn = psycopg2.connect(database="dvdrental", user='upraxis', password='upass', host='127.0.0.1', port= '5432')
    #Creating a cursor object using the cursor() method
    cursor = conn.cursor()
    try:
        cursor.execute(s)
        print('Command executed')
        conn.commit()
    except:
        print('Command failed')
    #Closing the connection
    conn.close()

In [ ]:
runSelect('select count(*) from film')

# Exercise 3 D

In [ ]:
# Reading the contents of the table
runSelect("select * from category id limit 5")

In [ ]:
runSelect("select * from film_category limit 5")

In [ ]:
runSelect("select * from film limit 5")

In [ ]:
runSelect("select * from language limit 5")

In [ ]:
runSelect("select * from film_actor limit 5")

In [ ]:
runSelect("select * from inventory limit 5")

In [ ]:
runSelect("select * from rental limit 5")

In [ ]:
runSelect("select * from payment limit 5")

In [ ]:
runSelect("select * from staff")

In [ ]:
runSelect("select * from actor limit 5")

In [ ]:
runSelect("select * from customer limit 5")

In [ ]:
runSelect("select * from address limit 5")

In [ ]:
runSelect("select * from city limit 5")

In [ ]:
runSelect("select * from country limit 5")

In [ ]:
runSelect("select * from store limit 5")

# Basic Query

In [ ]:
runSelect("select * from film where length = 180")

In [ ]:
runSelect("select first_name ||' '|| last_name as name, email from customer where address_id = 23")

In [ ]:
runSelect("select * from film where description like '%India%' and length < 60")

In [ ]:
runSelect("select * from payment limit 5 offset 10")

In [ ]:
runSelect("select customer_id, case when (return_date - rental_date) > '10' then 'late' else 'on_time' end as timeline from rental order by customer_id")

In [ ]:
runSelect("select rental_id, case when amount > 5.00 then 'expensive' else 'cheap' end as cost from payment order by rental_id limit 10")

In [ ]:
runSelect("select first_name from customer where first_name like 'K%' order by first_name desc")

In [ ]:
runSelect("select first_name ||' '|| last_name as name, length(first_name ||' '|| last_name) as len from customer order by len desc limit 20")

In [ ]:
runSelect("select inventory_id, rental_date from rental where rental_date between '2005-06-01' and '2005-07-01'")

In [ ]:
runSelect("select distinct first_name from actor order by first_name limit 10")

In [ ]:
runSelect("select max(rental_date) as last_rental from rental")

In [ ]:
runSelect("select customer_id, rental_date from rental where rental_date = (select max(rental_date) from rental) order by customer_id")

In [ ]:
runSelect("select first_name, last_name from actor where first_name = 'Johnny' or last_name = 'Davis'")

In [ ]:
runSelect("select * from address where district in ('Alberta', 'QLD', 'Nagasaki')")

In [ ]:
runSelect("select * from film where rating = 'R' and length < 60")

In [ ]:
runSelect("select first_name ||' '|| last_name as name from customer order by first_name ||' '|| last_name offset 5 rows fetch first 5 rows only")

In [ ]:
runSelect("select payment_id, amount, payment_date from payment where payment_date::date in ('2007-02-15', '2007-02-16') limit 10")

In [ ]:
runSelect("select payment_id, amount, payment_date from payment where (payment_date between '2007-02-16' and '2007-02-20') and amount = 0.99 or amount = 7.99")

In [ ]:
runSelect("select * from customer where last_name between 'Da' and 'He' order by last_name")

In [ ]:
runSelect("select address, address2 from address where address2 is null")

In [ ]:
runSelect("select address, address2 from address where address2 is not null limit 10")

In [ ]:
runSelect("select rental_id, case when return_date > rental_date then 'Not Late' else 'Late' END AS late_status from rental limit 5")

In [ ]:
runSelect("SELECT title, CASE WHEN fc.category_id = 5 THEN 'Comedy' ELSE 'Not Comedy' END AS category FROM film f LEFT JOIN film_category fc ON f.film_id = fc.film_id limit 5")

In [ ]:
runSelect("SELECT title, CASE WHEN fc.category_id = 1 THEN 'Horror' ELSE 'Not Horror' END AS category FROM film f LEFT JOIN film_category fc ON f.film_id = fc.film_id limit 5")

In [ ]:
runSelect("SELECT title, CASE WHEN l.name = 'English' THEN 'English' ELSE 'Not English' END AS language FROM film f JOIN language l ON f.language_id = l.language_id limit 5")

In [ ]:
runSelect("SELECT r.rental_id, CASE WHEN p.payment_id IS NOT NULL THEN 'Paid' ELSE 'Not Paid' END AS payment_status FROM rental r LEFT JOIN payment p ON r.rental_id = p.rental_id limit 5")

In [ ]:
runSelect("SELECT payment_id, CASE WHEN amount < 0 THEN 'Cash' ELSE 'Not Cash' END AS payment_type FROM payment limit 5")

In [ ]:
runSelect("SELECT f.title, CASE WHEN i.inventory_id IS NOT NULL THEN 'Available' ELSE 'Not Available' END AS availability FROM film f LEFT JOIN inventory i ON f.film_id = i.film_id limit 5")

In [ ]:
runSelect("SELECT r.customer_id, CASE WHEN COUNT(r.rental_id) > 5 THEN 'Frequent Renter' ELSE 'Not Frequent Renter' END AS rental_frequency FROM rental r GROUP BY r.customer_id limit 5")

In [ ]:
runSelect("SELECT f.title, CASE WHEN COUNT(fa.actor_id) > 3 THEN 'Many Actors' ELSE 'Few Actors' END AS actor_count FROM film f LEFT JOIN film_actor fa ON f.film_id = fa.film_id GROUP BY f.title limit 5")

In [ ]:
runSelect("SELECT title, CASE WHEN rating = 'R' THEN 'High Rental Rate' ELSE 'Low Rental Rate' END AS rental_rate FROM film limit 5")

In [ ]:
runSelect("SELECT p.customer_id, CASE WHEN SUM(p.amount) > 100 THEN 'Large Payment' ELSE 'Small Payment' END AS payment_size FROM payment p GROUP BY p.customer_id limit 5")

In [ ]:
runSelect("SELECT r.customer_id, CASE WHEN COUNT(r.rental_id) > 3 THEN 'Multiple Rentals' ELSE 'Single Rental' END AS rental_frequency FROM rental r GROUP BY r.customer_id limit 5")

In [ ]:
runSelect("SELECT f.title, CASE WHEN i.inventory_id IS NOT NULL THEN 'Available' ELSE 'Not Available' END AS availability FROM film f LEFT JOIN inventory i ON f.film_id = i.film_id limit 5")

In [ ]:
runSelect("SELECT payment_id, CASE WHEN amount > 50 THEN 'High Value' ELSE 'Low Value' END AS transaction_type FROM payment limit 5")

In [ ]:
runSelect("SELECT rental_id, CASE WHEN (return_date - rental_date) > '7' THEN 'Long-term' ELSE 'Short-term' END AS rental_duration FROM rental limit 5")

In [ ]:
runSelect("SELECT c.customer_id, CASE WHEN COUNT(r.rental_id) > 10 THEN 'Frequent Renter' ELSE 'Occasional Renter' END AS rental_frequency FROM customer c JOIN rental r ON c.customer_id = r.customer_id GROUP BY c.customer_id limit 5")

In [ ]:
runSelect("SELECT customer_id, CASE WHEN COUNT(rental_id) >= 20 THEN 'VIP' ELSE 'Regular' END AS customer_type FROM rental GROUP BY customer_id limit 5")

In [ ]:
runSelect("SELECT f.title, CASE WHEN c.name = 'Action' THEN 'Action' ELSE 'Other' END AS movie_genre FROM film f JOIN film_category fc ON f.film_id = fc.film_id JOIN category c ON fc.category_id = c.category_id limit 5")

In [ ]:
runSelect("SELECT f.title, CASE WHEN COUNT(r.rental_id) >= 100 THEN 'Popular' ELSE 'Not Popular' END AS popularity FROM film f LEFT JOIN inventory i ON f.film_id = i.film_id LEFT JOIN rental r ON i.inventory_id = r.inventory_id GROUP BY f.title limit 5")

In [ ]:
runSelect("SELECT c.customer_id, c.first_name, c.last_name, COUNT(r.rental_id) AS num_rentals, CASE WHEN COUNT(r.rental_id) > 50 THEN 'Premium' ELSE 'Regular' END AS customer_type FROM customer c LEFT JOIN rental r ON c.customer_id = r.customer_id GROUP BY c.customer_id, c.first_name, c.last_name limit 5")

# Joins and Subqueries

In [ ]:
runSelect("select p.*, cus.*\
from payment p \
INNER JOIN customer cus ON p.customer_id = cus.customer_id \
limit 10")

In [ ]:
runSelect("select cus.*, p.* \
from customer cus \
LEFT JOIN payment p ON cus.customer_id = p.customer_id \
limit 10")

In [ ]:
runSelect("select p.*, cus.* \
from payment p \
RIGHT JOIN customer cus ON p.customer_id = cus.customer_id \
limit 10")

In [ ]:
runSelect("select p.*, cus.* \
from payment p \
INNER JOIN customer cus ON p.customer_id = cus.customer_id \
WHERE cus.customer_id = 1 \
limit 10")

In [ ]:
runSelect("select p.*, cus.*, sta.* \
from payment p \
INNER JOIN customer cus ON p.customer_id = cus.customer_id \
INNER JOIN staff sta ON p.staff_id = sta.staff_id \
limit 10")

In [ ]:
runSelect("select cus.customer_id, cus.first_name, cus.last_name, SUM(p.amount) AS total_payment \
FROM customer cus \
LEFT JOIN payment p ON cus.customer_id = p.customer_id \
group by cus.customer_id, cus.first_name, cus.last_name \
limit 10")

In [ ]:
runSelect("select p.*, cus.* \
from payment p \
INNER JOIN customer cus ON p.customer_id = cus.customer_id \
order by p.amount desc \
limit 10")

In [ ]:
runSelect("select cus1.customer_id, cus1.first_name, cus1.last_name, p1.payment_date \
from payment p1 \
INNER JOIN payment p2 ON p1.customer_id = p2.customer_id \
INNER JOIN customer cus1 ON p1.customer_id = cus1.customer_id \
INNER JOIN customer cus2 ON p2.customer_id = cus2.customer_id \
where p1.payment_date = p2.payment_date \
and p1.payment_id <> p2.payment_id \
limit 10")

In [ ]:
runSelect("select cus.* \
from customer cus \
INNER JOIN ( \
    select customer_id, max(amount) as max_payment \
    from payment p \
    group by customer_id \
) as max_payments on cus.customer_id = max_payments.customer_id \
limit 10")

In [ ]:
runSelect("select cus.*, count(p.payment_id) as num_payments \
from customer cus \
LEFT JOIN payment p ON cus.customer_id = p.customer_id \
group by cus.customer_id \
having count(p.payment_id) > 5 \
limit 10")

In [ ]:
runSelect("select cus.* \
from customer cus \
where cus.customer_id not in ( \
    select DISTINCT customer_id \
    from payment \
) \
")

no records found


In [ ]:
runSelect("select cus.*, p.* \
from customer cus \
LEFT JOIN payment p ON cus.customer_id = p.customer_id \
where p.payment_id = ( \
    select payment_id \
    from payment \
    where customer_id = cus.customer_id \
    order by payment_date desc \
    limit 1 \
)\
limit 10")


In [ ]:
#runSelect("select cus.*, p.* \
#from customer cus \
#INNER JOIN payment p ON cus.customer_id = p.customer_id \
#and p.payment_date >= date_sub(current_date(), interval 1 month) limit 10")

In [ ]:
runSelect("select cus.*, p.* \
from customer cus \
LEFT JOIN payment p ON cus.customer_id = p.customer_id \
where p.amount IS NULL")

no records found


In [ ]:
runSelect("select p.*, cus.* \
from payment p, customer cus, address add, city c \
where p.customer_id = cus.customer_id \
and cus.address_id = add.address_id \
and add.city_id = c.city_id \
and c.city = 'Abu Dhabi' \
limit 10")

In [ ]:
runSelect("select cus1.customer_id, cus1.first_name, cus1.last_name, p1.payment_date \
from payment p1 \
INNER JOIN payment p2 ON p1.payment_date = p2.payment_date \
INNER JOIN customer cus1 ON p1.customer_id = cus1.customer_id \
INNER JOIN customer cus2 ON p2.customer_id = cus2.customer_id \
where cus1.customer_id <> cus2.customer_id \
limit 10")

In [ ]:
runSelect("select p.*, cus.* \
from payment p \
INNER JOIN customer cus ON p.customer_id = cus.customer_id \
where cus.customer_id < 10 \
UNION \
select p.*, cus.* \
from payment p \
INNER JOIN customer cus ON p.customer_id = cus.customer_id \
where cus.customer_id > 20 \
limit 10")

In [ ]:
runSelect("with TotalPayments as ( \
    select customer_id, sum(amount) as total_amount \
    from payment p\
    group by customer_id \
) \
select cus.*, TotalPayments.total_amount \
from customer cus \
LEFT JOIN TotalPayments ON cus.customer_id = TotalPayments.customer_id limit 10")

In [ ]:
runSelect("select cus.* \
from customer cus \
where exists ( \
    select 1 \
    from payment p \
    where p.customer_id = cus.customer_id \
)\
limit 10")

In [ ]:
runSelect("select f.*, fa.* \
from film f \
INNER JOIN film_actor fa ON f.film_id = fa.film_id limit 10")

In [ ]:
runSelect("select f.*, fa.* \
from film f \
LEFT JOIN film_actor fa ON f.film_id = fa.film_id \
limit 5")

In [ ]:
runSelect("select f.*, fa.* \
from film f \
RIGHT JOIN film_actor fa ON f.film_id = fa.film_id \
limit 5")

In [ ]:
runSelect("select f.*, fa.* \
from film f \
INNER JOIN film_actor fa ON f.film_id = fa.film_id \
where fa.actor_id = 10 \
limit 5")

In [ ]:
runSelect("select f.*, fa.*, cat.* \
from film f \
INNER JOIN film_actor fa ON f.film_id = fa.film_id \
INNER JOIN film_category fc ON f.film_id = fc.film_id \
INNER JOIN category cat ON fc.category_id = cat.category_id \
limit 5")

In [ ]:
runSelect("select f1.*, f2.* \
from film_actor as f1 \
INNER JOIN film_actor as f2 ON f1.actor_id = f2.actor_id \
INNER JOIN film as film1 ON f1.film_id = film1.film_id \
INNER JOIN film as film2 ON f2.film_id = film2.film_id \
where f1.film_id <> f2.film_id \
limit 5")

In [ ]:
runSelect("select distinct fa.actor_id, act.first_name, act.last_name, f.title, cat.name as category \
from actor act \
INNER JOIN film_actor fa ON act.actor_id = fa.actor_id \
INNER JOIN film f ON fa.film_id = f.film_id \
INNER JOIN film_category fc ON f.film_id = fc.film_id \
INNER JOIN category cat ON fc.category_id = cat.category_id \
where cat.name = 'Action' \
limit 5")

In [ ]:
runSelect("select act.* \
from actor act \
where act.actor_id NOT IN ( \
    select fa.actor_id \
    from film_actor fa \
    where fa.film_id = 1 \
) \
limit 5")

In [ ]:
runSelect("select a.actor_id, a.first_name, a.last_name, count(fa.film_id) as film_count \
from actor a \
LEFT JOIN film_actor fa ON a.actor_id = fa.actor_id \
group by a.actor_id, a.first_name, a.last_name \
limit 5")

In [ ]:
runSelect("select film.*, film_actor.* \
from film \
INNER JOIN film_actor ON film.film_id = film_actor.film_id \
and (film_actor.actor_id = 1 OR film_actor.actor_id = 2) \
limit 5")

In [ ]:
runSelect("select film.*, film_actor.* \
from film \
LEFT JOIN film_actor ON film.film_id = film_actor.film_id \
where film_actor.actor_id is null \
limit 5")

In [ ]:
runSelect("select film.*, film_actor.*, category.* \
from film, film_actor, film_category, category \
where film.film_id = film_actor.film_id \
and film.film_id = film_category.film_id \
and film_category.category_id = category.category_id \
and category.name = 'Comedy' \
limit 5")

In [ ]:
runSelect("select fa1.actor_id, fa2.actor_id, count(*) as film_count \
from film_actor fa1 \
INNER JOIN film_actor fa2 ON fa1.film_id = fa2.film_id \
where fa1.actor_id < fa2.actor_id \
group by fa1.actor_id, fa2.actor_id \
having count(*) > 1 \
limit 5")

In [ ]:
runSelect("select actor.*, film_actor.* \
from actor \
INNER JOIN film_actor ON actor.actor_id = film_actor.actor_id \
INNER JOIN film_category ON film_actor.film_id = film_category.film_id \
INNER JOIN category ON film_category.category_id = category.category_id \
where category.name = 'Action' \
UNION \
select actor.*, film_actor.* \
from actor \
INNER JOIN film_actor ON actor.actor_id = film_actor.actor_id \
INNER JOIN film_category ON film_actor.film_id = film_category.film_id \
INNER JOIN category ON film_category.category_id = category.category_id \
WHERE category.name = 'Drama' \
limit 5 \
")

In [ ]:
runSelect("with ActorFilms as ( \
    select actor.actor_id, actor.first_name, actor.last_name, film.* \
    from actor \
    INNER JOIN film_actor ON actor.actor_id = film_actor.actor_id \
    INNER JOIN film ON film_actor.film_id = film.film_id \
) \
select * from ActorFilms \
limit 5")

In [ ]:
runSelect("select film.*, film_actor.* \
from film \
cross join film_actor \
limit 5 \
")

In [ ]:
runSelect("select name, title, description, release_year, length, rating, special_features from category cat, film_category fc, film f where cat.category_id  =  fc.category_id and fc.film_id = f.film_id order by title limit 10")

In [ ]:
runSelect("select first_name||' '||last_name as name, rental_date, title, release_year, rental_duration from customer cus, inventory i, rental r, film f where cus.customer_id = r.customer_id and r.inventory_id = i.inventory_id and i.film_id = f.film_id order by first_name||' '||last_name limit 10")

In [ ]:
runSelect("select first_name||' '||last_name as actor_name, title, name as language from actor a, film_actor fa, film f, language l where a.actor_id = fa.actor_id and fa.film_id = f.film_id and f.language_id = l.language_id order by actor_name limit 20")

In [ ]:
runSelect("select first_name||' '||last_name as customer_name, address, city, country, amount from payment p, customer cus, address add, city c, country co where p.customer_id = cus.customer_id and cus.address_id = add.address_id and add.city_id = c.city_id and c.country_id = co.country_id order by customer_name offset 30 limit 10")

In [ ]:
runSelect("select * from store")

In [ ]:
runSelect("select cus.first_name||' '||cus.last_name as customer_name, sta.first_name||' '||sta.last_name as staff_name, sto.store_id, p.amount, p.payment_date from payment p, customer cus, store sto, staff sta where p.customer_id = cus.customer_id and cus.store_id = sto.store_id and sto.store_id = sta.store_id order by payment_date limit 20")

In [ ]:
runSelect("select r.rental_date as rented_on, f.film_id, f.title, f.rental_duration, p.payment_date from rental r, film f, payment p,staff sta, store sto, inventory inv where r.rental_id = p.rental_id and p.staff_id = sta.staff_id and sta.store_id = sto.store_id and sto.store_id = inv.store_id and inv.film_id = f.film_id and f.description like '%India%' and r.rental_date >= '2005-06-01' and r.rental_date < '2005-07-01' order by r.rental_date limit 10")

In [ ]:
runSelect("select f.film_id, f.title, inv.inventory_id, inv.store_id from film f LEFT OUTER JOIN inventory inv ON f.film_id = inv.film_id limit 10")

In [ ]:
runSelect("select fa.actor_id, f.film_id, f.title, f.release_year from film f LEFT OUTER JOIN film_actor fa ON f.film_id = fa.film_id limit 10")

In [ ]:
runSelect("select cus.first_name as cusfname, cus.last_name as cuslname, act.first_name as actfname, act.last_name as actlname from customer cus RIGHT OUTER JOIN actor act ON cus.customer_id = act.actor_id order by cusfname, cuslname offset 10 limit 20")

In [ ]:
runSelect("select cus.first_name||' '||cus.last_name as customer_name, f.film_id, f.title from customer cus RIGHT OUTER JOIN film f ON cus.customer_id = f.film_id where film_id in (133, 384) limit 20")

# Aggregates

In [ ]:
runSelect("select s.store_id, count(p.payment_id) as total_payments \
from store s \
LEFT JOIN staff st ON s.store_id = st.store_id \
LEFT JOIN payment p ON st.staff_id = p.staff_id \
group by s.store_id \
")

In [ ]:
runSelect("select s.store_id, sum(p.amount) as total_revenue \
from store s \
LEFT JOIN staff st ON s.store_id = st.store_id \
LEFT JOIN payment p ON st.staff_id = p.staff_id \
group by s.store_id")

In [ ]:
runSelect("select avg(p.amount) as avg_payment_amount \
from payment p \
JOIN customer c ON p.customer_id = c.customer_id \
")

In [ ]:
runSelect("select a.city_id, count(c.customer_id) as num_customers \
from customer c, address a \
where c.address_id = a.address_id \
group by a.city_id \
limit 5")

In [ ]:
runSelect("select c.customer_id, c.first_name, c.last_name, avg(r.return_date - r.rental_date) as avg_rental_duration_hours \
from customer c \
JOIN rental r ON c.customer_id = r.customer_id \
group by c.customer_id \
order by c.first_name limit 5")

In [ ]:
runSelect("select s.staff_id, count(r.rental_id) as total_rentals \
from staff s \
LEFT JOIN rental r ON s.staff_id = r.staff_id \
group by s.staff_id \
")

In [ ]:
runSelect("select s.staff_id, sum(p.amount) as total_revenue \
from staff s \
LEFT JOIN payment p ON s.staff_id = p.staff_id \
group by s.staff_id \
")

In [ ]:
runSelect("select c.customer_id, count(r.rental_id) as total_rentals, count(p.payment_id) as total_payments \
from customer c \
LEFT JOIN rental r ON c.customer_id = r.customer_id \
LEFT JOIN payment p ON c.customer_id = p.customer_id \
group by c.customer_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, avg(f.rental_rate) as avg_rental_rate \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select p.payment_id, count(*) as total_payments \
from payment p \
group by p.payment_id \
order by p.payment_id \
limit 5")

In [ ]:
runSelect("select s.store_id, st.staff_id, avg(p.amount) as avg_payment_amount \
from staff st \
JOIN payment p ON st.staff_id = p.staff_id \
JOIN store s ON st.store_id = s.store_id \
group by s.store_id, st.staff_id \
")

In [ ]:
runSelect("select l.language_id, l.name as language, count(f.film_id) as num_films \
from film f \
JOIN language l ON f.language_id = l.language_id \
group by l.language_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, count(f.film_id) as num_films \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select date(rental_date) as rental_day, count(*) as total_rentals \
from rental \
group by date(rental_date) \
limit 5")

In [ ]:
runSelect("select extract(month from payment_date) as payment_month, count(*) as total_payments \
from payment \
group by extract(month from payment_date) \
limit 5")

In [ ]:
runSelect("select s.store_id, count(distinct p.payment_id) as total_payments, count(distinct r.rental_id) as total_rentals \
from store s \
LEFT JOIN staff st ON s.store_id = st.store_id \
LEFT JOIN payment p ON st.staff_id = p.staff_id \
LEFT JOIN rental r ON st.staff_id = r.staff_id \
group by s.store_id \
")

In [ ]:
runSelect("select fc.category_id, avg(f.rental_rate) as avg_rental_rate, avg(f.replacement_cost) as avg_replacement_cost \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select s.store_id, sum(p.amount) as total_revenue, count(r.rental_id) as total_rentals \
from store s \
LEFT JOIN staff st ON s.store_id = st.store_id \
LEFT JOIN payment p ON st.staff_id = p.staff_id \
LEFT JOIN rental r ON st.staff_id = r.staff_id \
group by s.store_id \
limit 5")

In [ ]:
runSelect("select st.staff_id, count(r.rental_id) as total_rentals, count(p.payment_id) as total_payments \
from staff st \
LEFT JOIN rental r ON st.staff_id = r.staff_id \
LEFT JOIN payment p ON st.staff_id = p.staff_id \
group by st.staff_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, avg(r.return_date - r.rental_date) as avg_rental_duration \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
JOIN inventory i ON f.film_id = i.film_id \
JOIN rental r ON i.inventory_id = r.inventory_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, c.name AS category_name, count(*) as film_count \
from film_category fc \
INNER JOIN category c ON fc.category_id = c.category_id \
group by fc.category_id, c.name \
limit 5")

In [ ]:
runSelect("select customer_id, count(rental_id) as total_rentals \
from rental \
group by customer_id \
limit 5")

In [ ]:
runSelect("select sum(amount) as total_revenue \
from payment")

In [ ]:
runSelect("select avg(return_date - rental_date) as avg_rental_duration \
from rental")

In [ ]:
runSelect("select customer_id, avg(amount) as avg_payment_amount \
from payment \
group by customer_id \
limit 5")

In [ ]:
runSelect("select f.film_id, count(fa.actor_id) as num_actors \
from film_actor fa \
INNER JOIN film f ON fa.film_id = f.film_id \
group by f.film_id \
limit 5")

In [ ]:
runSelect("select film_id, count(inventory_id) as total_inventory \
from inventory \
group by film_id \
limit 5")

In [ ]:
runSelect("select film_id, avg(rental_rate) as avg_rental_rate \
from film \
group by film_id \
limit 5")

In [ ]:
runSelect("select staff_id, count(rental_id) as total_rentals \
from rental \
group by staff_id \
limit 5")

In [ ]:
runSelect("select language_id, avg(replacement_cost) as avg_replacement_cost \
from film \
group by language_id \
limit 5")

In [ ]:
runSelect("select customer_id, \
       max(amount) as max_payment_amount, \
       min(amount) as min_payment_amount \
from payment \
group by customer_id \
limit 5")

In [ ]:
runSelect("select rental_date, count(rental_id) as num_rentals \
from rental \
group by rental_date \
limit 5")

In [ ]:
runSelect("select s.store_id, count(payment_id) as total_payments \
from payment p \
INNER JOIN staff s ON p.staff_id = s.staff_id \
group by s.store_id")

In [ ]:
runSelect("select r.customer_id, avg(f.rental_rate) as avg_rental_rate \
from rental r \
INNER JOIN inventory i ON r.inventory_id = i.inventory_id \
INNER JOIN film f ON i.film_id = f.film_id \
group by r.customer_id \
limit 5")

In [ ]:
runSelect("select c.name as category_name, count(r.rental_id) as total_rentals \
from rental r \
INNER JOIN inventory i ON r.inventory_id = i.inventory_id \
INNER JOIN film f ON i.film_id = f.film_id \
INNER JOIN film_category fc ON f.film_id = fc.film_id \
INNER JOIN category c ON fc.category_id = c.category_id \
group by c.name \
limit 5")

In [ ]:
runSelect("select i.store_id, avg(f.replacement_cost) as avg_replacement_cost \
from inventory i \
INNER JOIN film f ON i.film_id = f.film_id \
group by i.store_id \
limit 5")

In [ ]:
runSelect("select s.store_id, p.staff_id, count(p.payment_id) as total_payments \
from payment p \
INNER JOIN staff s ON p.staff_id = s.staff_id \
group by s.store_id, p.staff_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, count(*) as num_films \
from film_category fc \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select f.language_id, count(*) as num_films \
from film f \
group by f.language_id \
limit 5")

In [ ]:
runSelect("select count(*) as num_rentals \
from rental \
limit 5")

In [ ]:
runSelect("select count(*) as num_payments \
from payment \
limit 5")

In [ ]:
runSelect("select a.city_id, count(*) as num_customers \
from customer c \
JOIN address a ON c.address_id = a.address_id \
group by a.city_id \
limit 5")

In [ ]:
runSelect("select s.store_id, count(*) as num_staff \
from staff s \
group by s.store_id")

In [ ]:
runSelect("select r.staff_id, count(*) as num_rentals \
from rental r \
group by r.staff_id")

In [ ]:
runSelect("select r.customer_id, count(*) as num_rentals \
from rental r \
group by r.customer_id \
limit 5")

In [ ]:
runSelect("select p.customer_id, count(*) as num_payments \
from payment p \
group by p.customer_id \
limit 5")

In [ ]:
runSelect("select p.customer_id, sum(p.amount) as total_amount_paid \
from payment p \
group by p.customer_id \
limit 5")

In [ ]:
runSelect("select s.staff_id, sum(p.amount) as total_amount_paid \
from staff s \
JOIN payment p ON s.staff_id = p.staff_id \
group by s.staff_id")

In [ ]:
runSelect("select i.film_id, count(*) as num_rentals \
from inventory i \
JOIN rental r ON i.inventory_id = r.inventory_id \
group by i.film_id")

In [ ]:
runSelect("select p.staff_id, count(*) as num_payments \
from payment p \
group by p.staff_id \
")

In [ ]:
runSelect("select r.staff_id, sum(p.amount) as total_revenue \
from rental r \
JOIN payment p ON r.rental_id = p.rental_id \
group by r.staff_id")

In [ ]:
runSelect("select r.rental_id, extract(hour from avg(r.return_date - r.rental_date)) as avg_rental_duration_hours \
from rental r \
group by r.rental_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, f.language_id, count(*) as num_films \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
group by fc.category_id, f.language_id \
limit 5")

In [ ]:
runSelect("select r.staff_id, extract(month from r.rental_date) as rental_month, count(*) as num_rentals \
from rental r \
group by r.staff_id, extract(month from r.rental_date) \
limit 5")

In [ ]:
runSelect("select p.customer_id, extract(month from p.payment_date) as payment_month, count(*) as num_payments \
from payment p \
group by p.customer_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select p.staff_id, extract(month from p.payment_date) as payment_month, sum(p.amount) as total_revenue \
from payment p \
group by p.staff_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select fc.category_id, count(*) as num_rentals \
from film_category fc \
JOIN inventory i ON fc.film_id = i.film_id \
JOIN rental r ON i.inventory_id = r.inventory_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select r.customer_id, count(*) as num_rentals \
from rental r \
group by r.customer_id \
limit 5")

In [ ]:
runSelect("select p.staff_id, extract(month from p.payment_date) as payment_month, count(*) as num_payments \
from payment p \
group by p.staff_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select fc.category_id, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film_category fc ON i.film_id = fc.film_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select r.customer_id, extract(month from r.rental_date) as rental_month, count(*) as num_rentals \
from rental r \
group by r.customer_id, extract(month from r.rental_date) \
limit 5")

In [ ]:
runSelect("select fc.category_id, count(*) as num_payments \
from film_category fc \
JOIN inventory i ON fc.film_id = i.film_id \
JOIN rental r ON i.inventory_id = r.inventory_id \
JOIN payment p ON r.rental_id = p.rental_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, avg(f.replacement_cost) as avg_replacement_cost \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
group by fc.category_id \
")

In [ ]:
runSelect("select r.customer_id, extract(day from r.rental_date) as rental_day, count(*) as num_rentals \
from rental r \
group by r.customer_id, extract(day from r.rental_date) \
limit 5")

In [ ]:
runSelect("select i.film_id, r.staff_id, sum(p.amount) as total_revenue \
from rental r \
JOIN payment p ON r.rental_id = p.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
group by i.film_id, r.staff_id \
limit 5")

In [ ]:
runSelect("select fc.category_id, avg(f.rental_rate) as avg_rental_rate \
from film_category fc \
JOIN film f ON fc.film_id = f.film_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select r.staff_id, count(*) as num_rentals \
from rental r \
group by r.staff_id \
limit 5")

In [ ]:
runSelect("select r.staff_id, count(*) as num_rentals \
from rental r \
group by r.staff_id \
limit 5")

In [ ]:
runSelect("select r.staff_id, extract(day from r.rental_date) as rental_day, sum(p.amount) as total_revenue \
from rental r \
JOIN payment p ON r.rental_id = p.rental_id \
group by r.staff_id, extract(day from r.rental_date) \
limit 5")

In [ ]:
runSelect("select p.payment_id, extract(month from p.payment_date) as payment_month, count(*) as num_payments \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
group by p.payment_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select fc.category_id, extract(hour from avg(r.return_date - r.rental_date)) as avg_rental_duration_hours \
from rental r \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film_category fc ON i.film_id = fc.film_id \
group by fc.category_id \
limit 5")

In [ ]:
runSelect("select r.rental_id, extract(month from r.rental_date) as rental_month, count(*) as num_rentals \
from rental r \
group by r.rental_id, extract(month from r.rental_date) \
limit 5")

In [ ]:
runSelect("select p.customer_id, extract(year from p.payment_date) as payment_year, count(*) as num_payments \
from payment p \
group by p.customer_id, extract(year from p.payment_date) \
limit 5")

In [ ]:
runSelect("select r.staff_id, extract(month from p.payment_date) as payment_month, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
group by r.staff_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select r.rental_id, extract(year from r.rental_date) as rental_year, count(*) as num_rentals \
from rental r \
group by r.rental_id, extract(year from r.rental_date) \
limit 5")

In [ ]:
runSelect("select p.staff_id, extract(year from p.payment_date) as payment_year, count(*) as num_payments \
from payment p \
group by p.staff_id, extract(year from p.payment_date) \
limit 5")

In [ ]:
runSelect("select p.customer_id, extract(month from p.payment_date) as payment_month, sum(p.amount) as total_revenue \
from payment p \
group by p.customer_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select r.staff_id, extract(year from r.rental_date) as rental_year, count(*) as num_rentals \
from rental r \
group by r.staff_id, extract(year from r.rental_date) \
limit 5")

In [ ]:
runSelect("select i.film_id, i.store_id, extract(month from p.payment_date) as payment_month, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
GROUP BY i.film_id, i.store_id, extract(month from p.payment_date) \
limit 5")

In [ ]:
runSelect("select r.staff_id, r.customer_id, f.film_id, fc.category_id, f.language_id, i.store_id, count(*) as num_rentals \
from rental r \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film f ON i.film_id = f.film_id \
JOIN film_category fc ON f.film_id = fc.film_id \
group by r.staff_id, r.customer_id, f.film_id, fc.category_id, f.language_id, i.store_id \
limit 5")

In [ ]:
runSelect("select p.staff_id, r.customer_id, f.film_id, fc.category_id, f.language_id, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film f ON i.film_id = f.film_id \
JOIN film_category fc ON f.film_id = fc.film_id \
group by p.staff_id, r.customer_id, f.film_id, fc.category_id, f.language_id \
limit 5")

In [ ]:
runSelect("select p.staff_id, r.customer_id, f.film_id, fc.category_id, f.language_id, count(*) as num_payments \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film f ON i.film_id = f.film_id \
JOIN film_category fc ON f.film_id = fc.film_id \
group by p.staff_id, r.customer_id, f.film_id, fc.category_id, f.language_id \
limit 5")

#Date

In [ ]:
runSelect("select * \
from rental \
where rental_date = ('2005-06-16 12:00:00'::timestamp) \
limit 5")

no records found


In [ ]:
runSelect("select * \
from payment \
where payment_date = ('2005-06-16 12:00:00'::timestamp) \
limit 5")

no records found


In [ ]:
runSelect("select * \
from payment \
where payment_date = ('2005-06-16 12:00:00'::timestamp) \
limit 5")

no records found


In [ ]:
runSelect("select * \
from rental \
where rental_date between '2005-02-14' and '2005-02-16' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from payment \
where payment_date between '2005-02-16' and '2005-02-18' \
limit 5")

no records found


In [ ]:
runSelect("select ('2005-06-16 12:00:00'::timestamp) as rental_day, count(*) as num_rentals \
from rental \
group by rental_day \
limit 5")

In [ ]:
runSelect("select ('2005-06-16 12:00:00'::timestamp) as payment_day, count(*) as num_payments \
from payment \
group by payment_day \
limit 5")

In [ ]:
runSelect("select * \
from rental \
where rental_date > '2005-07-14' \
limit 5")

In [ ]:
runSelect("select * \
from payment \
where payment_date > '2005-07-16' \
limit 5")

In [ ]:
runSelect("select * \
from rental \
where rental_date < '2005-06-11' \
limit 5")

In [ ]:
runSelect("select * \
from payment \
where payment_date < '2005-06-11' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from rental \
where customer_id = 5 \
and rental_date = '2005-06-11' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from payment \
where customer_id = 5 \
and payment_date = '2005-06-11' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from rental \
where staff_id = 1 \
and rental_date = '2005-06-11' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from payment \
where staff_id = 2 \
and payment_date = '2005-06-12' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from rental \
where rental_date = '2005-06-12' \
limit 5")

no records found


In [ ]:
runSelect("select * \
from payment \
where rental_id in ( \
    select rental_id \
    from rental \
    where rental_id = 1 \
) \
and payment_date = '2005-06-11' \
limit 5")

no records found


In [ ]:
runSelect("select fc.category_id, ('2005-06-16 12:00:00'::timestamp) as payment_day, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film_category fc ON i.film_id = fc.film_id \
group by fc.category_id, payment_day \
limit 5")

In [ ]:
runSelect("select f.language_id, ('2005-06-16 12:00:00'::timestamp) as rental_day, sum(r.return_date - r.rental_date) as total_rental_duration \
from rental r \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film f ON i.film_id = f.film_id \
group by f.language_id, rental_day \
limit 5")

In [ ]:
runSelect("select f.language_id, ('2005-06-16 12:00:00'::timestamp) as payment_day, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film f ON i.film_id = f.film_id \
group by f.language_id, payment_day \
limit 5")

In [ ]:
runSelect("select c.country_id,('2005-06-16 12:00:00'::timestamp) as rental_day, sum(r.return_date - r.rental_date) as total_rental_duration \
from rental r \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film f ON i.film_id = f.film_id \
JOIN language l ON f.language_id = l.language_id \
JOIN country c ON l.language_id = c.country_id \
group by c.country_id, rental_day \
limit 5")

In [ ]:
runSelect("select fc.category_id,('2005-07-16 12:00:00'::timestamp::date) as payment_day, sum(p.amount) as total_revenue \
from payment p \
JOIN rental r ON p.rental_id = r.rental_id \
JOIN inventory i ON r.inventory_id = i.inventory_id \
JOIN film_category fc ON i.film_id = fc.film_id \
JOIN film f ON i.film_id = f.film_id \
WHERE f.language_id = 1 \
GROUP BY fc.category_id, payment_day \
limit 5")

#Chronobooks <br>
Two science fiction novels by Prithwis Mukerjee. A dystopian Earth. A technocratic society managed by artificial intelligence. Escape and epiphany on Mars. Can man and machine, carbon and silicon explore and escape into other dimensions of existence? An Indic perspective rooted in Advaita Vedanta and the Divine Feminine.  [More information](http://bit.ly/chronobooks) <br>
![alt text](https://github.com/Praxis-QR/RDWH/raw/main/images/CTCYFooter-1.png)

In [ ]:
from datetime import datetime
import pytz
print('tested',datetime.now(pytz.timezone('Asia/Calcutta')))

#This Notebook consists of four parts. In total there are 200 queries out of which 41 are basic queries, 45 queries are on join, 90 queries are on aggregates, and 24 queries are on date.